# Solving a complex task with a multi-agent hierarchy

This notebook is part of the [Hugging Face Agents Course](https://www.hf.co/learn/agents-course), a free Course from beginner to expert, where you learn to build Agents.

![Agents course share](https://huggingface.co/datasets/agents-course/course-images/resolve/main/en/communication/share.png)

The reception is approaching! With your help, Alfred is now nearly finished with the preparations.

But now there's a problem: the Batmobile has disappeared. Alfred needs to find a replacement, and find it quickly.

Fortunately, a few biopics have been done on Bruce Wayne's life, so maybe Alfred could get a car left behind on one of the movie set, and re-engineer it up to modern standards, which certainly would include a full self-driving option.

But this could be anywhere in the filming locations around the world - which could be numerous.

So Alfred wants your help. Could you build an agent able to solve this task?

> 👉 Find all Batman filming locations in the world, calculate the time to transfer via a cargo plane to there, and represent them on a map, with a color varying by a cargo plane transfer time. Also represent some supercar factories with the same cargo plane transfer time.

Let's build this!

# Multi-Agent Systems
Multi-agent systems enable specialized agents to collaborate on complex tasks, improving modularity, scalability, and robustness. Instead of relying on a single agent, tasks are distributed among agents with distinct capabilities.

In smolagents, different agents can be combined to generate Python code, call external tools, perform web searches, and more. By orchestrating these agents, we can create powerful workflows.

A typical setup might include:

- A Manager Agent for task delegation
- A Code Interpreter Agent for code execution
- A Web Search Agent for information retrieval
The diagram below illustrates a simple multi-agent architecture where a Manager Agent coordinates a Code Interpreter Tool and a Web Search Agent, which in turn utilizes tools like the DuckDuckGoSearchTool and VisitWebpageTool to gather relevant information.

![multiagent](../../image/multi-agent.png)

## Solving a complex task with a multi-agent hierarchy
The reception is approaching! With your help, Alfred is now nearly finished with the preparations.

But now there’s a problem: **the Batmobile has disappeared**. Alfred needs to find a replacement, and find it quickly.

Fortunately, a few biopics have been done on Bruce Wayne’s life, so maybe Alfred could get a car left behind on one of the movie sets, and re-engineer it up to modern standards, which certainly would include a full self-driving option.

But this could be anywhere in the filming locations around the world - which could be numerous.

So Alfred wants your help. Could you build an agent able to solve this task?


In [1]:
!pip install 'smolagents[litellm]' plotly geopandas shapely kaleido -q

In [22]:
import pandas as pd

In [5]:
from huggingface_hub import notebook_login, whoami



In [ ]:
notebook_login()

In [ ]:
whoami()

In [7]:
# We first make a tool to get the cargo plane transfer time.
import math
from typing import Optional, Tuple

from smolagents import tool


@tool
def calculate_cargo_travel_time(
    origin_coords: Tuple[float, float],
    destination_coords: Tuple[float, float],
    cruising_speed_kmh: Optional[float] = 750.0,  # Average speed for cargo planes
) -> float:
    """
    Calculate the travel time for a cargo plane between two points on Earth using great-circle distance.

    Args:
        origin_coords: Tuple of (latitude, longitude) for the starting point
        destination_coords: Tuple of (latitude, longitude) for the destination
        cruising_speed_kmh: Optional cruising speed in km/h (defaults to 750 km/h for typical cargo planes)

    Returns:
        float: The estimated travel time in hours

    Example:
        >>> # Chicago (41.8781° N, 87.6298° W) to Sydney (33.8688° S, 151.2093° E)
        >>> result = calculate_cargo_travel_time((41.8781, -87.6298), (-33.8688, 151.2093))
    """

    def to_radians(degrees: float) -> float:
        return degrees * (math.pi / 180)

    # Extract coordinates
    lat1, lon1 = map(to_radians, origin_coords)
    lat2, lon2 = map(to_radians, destination_coords)

    # Earth's radius in kilometers
    EARTH_RADIUS_KM = 6371.0

    # Calculate great-circle distance using the haversine formula
    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = (
        math.sin(dlat / 2) ** 2
        + math.cos(lat1) * math.cos(lat2) * math.sin(dlon / 2) ** 2
    )
    c = 2 * math.asin(math.sqrt(a))
    distance = EARTH_RADIUS_KM * c

    # Add 10% to account for non-direct routes and air traffic controls
    actual_distance = distance * 1.1

    # Calculate flight time
    # Add 1 hour for takeoff and landing procedures
    flight_time = (actual_distance / cruising_speed_kmh) + 1.0

    # Format the results
    return round(flight_time, 2)


print(calculate_cargo_travel_time((41.8781, -87.6298), (-33.8688, 151.2093)))

22.82


For the model provider, we use Together AI, one of the new [inference providers on the Hub](https://huggingface.co/blog/inference-providers)!

Regarding the GoogleSearchTool: this requires either having setup env variable `SERPAPI_API_KEY` and passing `provider="serpapi"` or having `SERPER_API_KEY` and passing `provider=serper`.

If you don't have any Serp API provider setup, you can use `DuckDuckGoSearchTool` but beware that it has a rate limit.

In [8]:
import os
from PIL import Image
from smolagents import CodeAgent, GoogleSearchTool, InferenceClientModel, VisitWebpageTool


model = InferenceClientModel(model_id="Qwen/Qwen2.5-Coder-32B-Instruct", provider="together")

We can start with creating a baseline, simple agent to give us a simple report.

In [9]:
task = """Find all Batman filming locations in the world, calculate the time to transfer via cargo plane to here (we're in Gotham, 40.7128° N, 74.0060° W), and return them to me as a pandas dataframe.
Also give me some supercar factories with the same cargo plane transfer time."""

In [27]:
import os
from dotenv import load_dotenv

load_dotenv()


SERPER_API_KEY = os.getenv("SERPAPI_API_KEY")


In [19]:
agent = CodeAgent(
    model=model,
    tools=[GoogleSearchTool(), VisitWebpageTool(), calculate_cargo_travel_time],
    additional_authorized_imports=["pandas"],
    max_steps=20,
)

In [20]:
result = agent.run(task)

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ Find all Batman filming locations in the world, calculate the time to transfer via cargo plane to here (we're   │
│ in Gotham, 40.7128° N, 74.0060° W), and return them to me as a pandas dataframe.                                │
│ Also give me some supercar factories with the same cargo plane transfer time.                                   │
│                                                                                                                 │
╰─ InferenceClientModel - Qwen/Qwen2.5-Coder-32B-Instruct ────────────────────────────────────────────────────────╯

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  batman_locations = web_search(query="Batman filming locations")                                                  
  print(batman_locations)                                                                                          
 ─────────────────────────────────────────────────────────────────────────────────────────────────────────────────

Execution logs:
## Search Results
0. [The Batman (2022) - Filming & production](https://www.imdb.com/title/tt1877830/locations/)
Source: IMDb

Filming locations: Necropolis Cemetery, Glasgow, Scotland, UK (Batman and Selina leaving the cemetery) Helpful•87 1
St. George's Hall, Liverpool, England, UK

1. [The Batman | Film Locations](https://movie-locations.com/movies/b/The-Batman-2022-2.php)
Source: The Worldwide Guide To Movie Locations

The Batman filming location: St George's Hall, Liverpool · The Batman filming location: Royal Liver Building, Pier 
Head, Liverpool · The Batman filming location: ...

2. [Batman (1989) - Filming & production](https://www.imdb.com/title/tt0096895/locations/)
Source: IMDb

Filming locations ; Knebworth House, Knebworth, Hertfordshire, England, UK. (Wayne Manor; exterior) · 21 ; Acton 
Lane Power Station, Acton Lane, Acton, London, ...

3. [Where was The Batman filmed? ALL the Filming Locations 
...](https://www.atlasofwonders.com/2022/04/where-was-the-batman-filmed.html)
Source: Atlas of Wonders

Guide to the all the filming locations of The Batman - The 2022 movie with Robert Pattison filmed in Chicago and 
The UK - The City and the Wayne House.

4. [12 Batman Movie Locations You Can 
Visit!](https://www.travelandleisureasia.com/global/destinations/batman-movie-locations-you-can-visit/)
Date published: Jan 10, 2023
Source: Travel and Leisure Asia

Most of the filming of Batman movies is done in the Warner Bros studios and across the US, including New York and 
Pittsburgh. You will notice ...

5. [Batman Movies and Filming Locations in Los 
Angeles](https://www.traveltodayla.com/post/batman-movies-in-la?srsltid=AfmBOooiWKOoGPtvv50vJi28YvH5SMnIUtjVkWqbzpx
-Foh7PJBgSiHc)
Date published: Apr 20, 2023
Source: LA Today

Batman Movies and Filming Locations in LA · Cliffs of Marineland · Kirkeby Center · Gateway East Building · Wayne 
Manor · Bronson Caves · Batman ...

6. [Some photos from the filming locations in downtown 
...](https://www.reddit.com/r/DC_Cinematic/comments/1dkfuqz/some_photos_from_the_filming_locations_in/)
Source: Reddit · r/DC_Cinematic

r/batman - The Batman movie filming location // Thompson Center Downtown Chicago ... THE BATMAN - Liverpool Filming
Locations - new video, a watch ...

7. [The Batman (2022) Locations](https://www.latlong.net/location/the-batman-2022-locations-427)
Source: Latitude and Longitude Finder

The Batman (2022) was filmed in 2 Temple Pl, 230 S LaSelle St, 91 Wishart St, Anfield Cemetery, Cardington Studios,
Central Saint Martins, Chicago (exterior), ...

8. [Where was Batman filmed?](https://giggster.com/guide/movie-location/where-was-batman-filmed)
Source: Giggster

Most scenes were shot in and around these three regions, including Wayne Manor, the Axis Chemical Works, and the 
offices of the Gotham Globe.

Out: None

[Step 1: Duration 3.00 seconds| Input tokens: 2,285 | Output tokens: 165]

...

[Step 4: Duration 14.66 seconds| Input tokens: 16,768 | Output tokens: 2,607]

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 5 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  final_answer((batman_df, supercar_df))                                                                           
 ─────────────────────────────────────────────────────────────────────────────────────────────────────────────────

Out - Final answer: (                                            Location  Travel Time (hours)
0         Necropolis Cemetery, Glasgow, Scotland, UK                 8.60
1          St. George's Hall, Liverpool, England, UK                 8.81
2  Royal Liver Building, Pier Head, Liverpool, En...                 8.81
3  Knebworth House, Knebworth, Hertfordshire, Eng...                 9.14
4  Acton Lane Power Station, Acton Lane, Acton, L...                 9.16
5                                 Chicago (exterior)                 2.68
6     Cardington Studios, Hertfordshire, England, UK                 9.14
7         Central Saint Martins, London, England, UK                 9.17
8        Bronson Caves, Los Angeles, California, USA                 6.78
9   Thompson Center, Downtown Chicago, Illinois, USA                 2.68,                                     
Factory  Travel Time (hours)
0                 Ferrari, Maranello, Italy                10.72
1  Lamborghini, Sant'Agata Bolognese, Italy                10.77
2     Pagani, San Cesario sul Panaro, Italy                10.72
3                    Ducati, Bologna, Italy                10.77
4                Noble, Crewe, Cheshire, UK                 8.85
5      Sly Garage Factory, Maranello, Italy                10.72
6               McLaren, Woking, Surrey, UK                 9.13)

[Step 5: Duration 15.35 seconds| Input tokens: 24,529 | Output tokens: 2,664]

In [21]:
result

(                                            Location  Travel Time (hours)
 0         Necropolis Cemetery, Glasgow, Scotland, UK                 8.60
 1          St. George's Hall, Liverpool, England, UK                 8.81
 2  Royal Liver Building, Pier Head, Liverpool, En...                 8.81
 3  Knebworth House, Knebworth, Hertfordshire, Eng...                 9.14
 4  Acton Lane Power Station, Acton Lane, Acton, L...                 9.16
 5                                 Chicago (exterior)                 2.68
 6     Cardington Studios, Hertfordshire, England, UK                 9.14
 7         Central Saint Martins, London, England, UK                 9.17
 8        Bronson Caves, Los Angeles, California, USA                 6.78
 9   Thompson Center, Downtown Chicago, Illinois, USA                 2.68,
                                     Factory  Travel Time (hours)
 0                 Ferrari, Maranello, Italy                10.72
 1  Lamborghini, Sant'Agata Bolognese, Ita

We could already improve this a bit by throwing in some dedicated planning steps, and adding more prompting.

In [23]:
agent.planning_interval = 4

detailed_report = agent.run(f"""
You're an expert analyst. You make comprehensive reports after visiting many websites.
Don't hesitate to search for many queries at once in a for loop.
For each data point that you find, visit the source url to confirm numbers.

{task}
""")

print(detailed_report)

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ You're an expert analyst. You make comprehensive reports after visiting many websites.                          │
│ Don't hesitate to search for many queries at once in a for loop.                                                │
│ For each data point that you find, visit the source url to confirm numbers.                                     │
│                                                                                                                 │
│ Find all Batman filming locations in the world, calculate the time to transfer via cargo plane to here (we're   │
│ in Gotham, 40.7128° N, 74.0060° W), and return them to me as a pandas dataframe.                                │
│ Also give me some supercar factories with the same cargo plane transfer time.                                   │
│                                                                                                                 │
╰─ InferenceClientModel - Qwen/Qwen2.5-Coder-32B-Instruct ────────────────────────────────────────────────────────╯

────────────────────────────────────────────────── Initial plan ───────────────────────────────────────────────────
Here are the facts I know and the plan of action that I will follow to solve the task:
```
## 1. Facts survey

### 1.1. Facts given in the task
- Gotham coordinates: 40.7128° N, 74.0060° W
- We need to find Batman filming locations worldwide.
- We need to calculate the travel time for a cargo plane to Gotham for each filming location.
- We need to find supercar factories with the same cargo plane transfer time to Gotham.

### 1.2. Facts to look up
- List of Batman filming locations worldwide.
  - Source: Web search for "Batman filming locations" and verify from reliable sources like IMDb, official movie 
websites, or reputable news articles.
- Coordinates of each Batman filming location.
  - Source: Geocoding services or verified maps and location databases.
- Coordinates of supercar factories worldwide.
  - Source: Web search for "supercar factories" and verify from reliable sources like manufacturer websites or 
reputable automotive news sites.
- Cruising speed of a typical cargo plane.
  - Source: Aviation industry standards or reputable aviation websites.

### 1.3. Facts to derive
- Travel time for a cargo plane from each Batman filming location to Gotham.
  - Derivation: Use the `calculate_cargo_travel_time` function with the coordinates of each filming location and 
Gotham.
- Travel time for a cargo plane from each supercar factory to Gotham.
  - Derivation: Use the `calculate_cargo_travel_time` function with the coordinates of each supercar factory and 
Gotham.
- Comparison of travel times to identify supercar factories with similar travel times to Batman filming locations.
  - Derivation: Logical comparison of the calculated travel times.

## 2. Plan
1. Perform a web search for "Batman filming locations" and gather a list of locations.
2. Verify the list of Batman filming locations from reliable sources.
3. For each verified Batman filming location, find its coordinates.
4. Perform a web search for "supercar factories" and gather a list of factories.
5. Verify the list of supercar factories from reliable sources.
6. For each verified supercar factory, find its coordinates.
7. Perform a web search for the cruising speed of a typical cargo plane.
8. Use the `calculate_cargo_travel_time` function to calculate the travel time from each Batman filming location to
Gotham.
9. Use the `calculate_cargo_travel_time` function to calculate the travel time from each supercar factory to 
Gotham.
10. Create a pandas dataframe with Batman filming locations and their travel times to Gotham.
11. Identify supercar factories with similar travel times to Batman filming locations.
12. Add the identified supercar factories to the pandas dataframe.
13. Finalize the pandas dataframe with all relevant information.
14. Provide the final answer using the `final_answer` function.


```

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  batman_filming_locations = web_search(query="Batman filming locations")                                          
  print(batman_filming_locations)                                                                                  
 ─────────────────────────────────────────────────────────────────────────────────────────────────────────────────

Execution logs:
## Search Results
0. [The Batman (2022) - Filming & production](https://www.imdb.com/title/tt1877830/locations/)
Source: IMDb

Filming locations: Necropolis Cemetery, Glasgow, Scotland, UK (Batman and Selina leaving the cemetery) Helpful•87 1
St. George's Hall, Liverpool, England, UK

1. [The Batman | Film Locations](https://movie-locations.com/movies/b/The-Batman-2022-2.php)
Source: The Worldwide Guide To Movie Locations

The Batman filming location: St George's Hall, Liverpool · The Batman filming location: Royal Liver Building, Pier 
Head, Liverpool · The Batman filming location: ...

2. [Batman (1989) - Filming & production](https://www.imdb.com/title/tt0096895/locations/)
Source: IMDb

Filming locations ; Knebworth House, Knebworth, Hertfordshire, England, UK. (Wayne Manor; exterior) · 21 ; Acton 
Lane Power Station, Acton Lane, Acton, London, ...

3. [Where was The Batman filmed? ALL the Filming Locations 
...](https://www.atlasofwonders.com/2022/04/where-was-the-batman-filmed.html)
Source: Atlas of Wonders

Guide to the all the filming locations of The Batman - The 2022 movie with Robert Pattison filmed in Chicago and 
The UK - The City and the Wayne House.

4. [12 Batman Movie Locations You Can 
Visit!](https://www.travelandleisureasia.com/global/destinations/batman-movie-locations-you-can-visit/)
Date published: Jan 10, 2023
Source: Travel and Leisure Asia

Most of the filming of Batman movies is done in the Warner Bros studios and across the US, including New York and 
Pittsburgh. You will notice ...

5. [Batman Movies and Filming Locations in Los 
Angeles](https://www.traveltodayla.com/post/batman-movies-in-la?srsltid=AfmBOooiWKOoGPtvv50vJi28YvH5SMnIUtjVkWqbzpx
-Foh7PJBgSiHc)
Date published: Apr 20, 2023
Source: LA Today

Batman Movies and Filming Locations in LA · Cliffs of Marineland · Kirkeby Center · Gateway East Building · Wayne 
Manor · Bronson Caves · Batman ...

6. [Some photos from the filming locations in downtown 
...](https://www.reddit.com/r/DC_Cinematic/comments/1dkfuqz/some_photos_from_the_filming_locations_in/)
Source: Reddit · r/DC_Cinematic

r/batman - The Batman movie filming location // Thompson Center Downtown Chicago ... THE BATMAN - Liverpool Filming
Locations - new video, a watch ...

7. [The Batman (2022) Locations](https://www.latlong.net/location/the-batman-2022-locations-427)
Source: Latitude and Longitude Finder

The Batman (2022) was filmed in 2 Temple Pl, 230 S LaSelle St, 91 Wishart St, Anfield Cemetery, Cardington Studios,
Central Saint Martins, Chicago (exterior), ...

8. [Where was Batman filmed?](https://giggster.com/guide/movie-location/where-was-batman-filmed)
Source: Giggster

Most scenes were shot in and around these three regions, including Wayne Manor, the Axis Chemical Works, and the 
offices of the Gotham Globe.

Out: None

...

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 9 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  # Filter supercar factories to match the travel time of Batman filming locations                                 
  batman_travel_times = batman_df['travel_time'].unique()                                                          
  filtered_supercar_df = supercar_df[supercar_df['travel_time'].isin(batman_travel_times)]                         
                                                                                                                   
  # Combine the dataframes into a final answer                                                                     
  final_df = pd.concat([batman_df, filtered_supercar_df], ignore_index=True)                                       
                                                                                                                   
  # Print the final dataframe                                                                                      
  print(final_df)                                                                                                  
                                                                                                                   
  # Provide the final answer using the final_answer function                                                       
  final_answer(final_df)                                                                                           
 ─────────────────────────────────────────────────────────────────────────────────────────────────────────────────

Execution logs:
                               name         city country  \
0               Necropolis Cemetery      Glasgow      UK   
1                 St. George's Hall    Liverpool      UK   
2   Royal Liver Building, Pier Head    Liverpool      UK   
3                Chicago (exterior)      Chicago     USA   
4                Cardington Studios   Cardington      UK   
5             Central Saint Martins       London      UK   
6                     Bronson Caves  Los Angeles     USA   
7                   Thompson Center      Chicago     USA   
8            Wayne Manor (exterior)  Los Angeles     USA   
9              Cliffs of Marineland  Los Angeles     USA   
10                   Kirkeby Center  Los Angeles     USA   
11            Gateway East Building  Los Angeles     USA   
12              Axis Chemical Works  Los Angeles     USA   
13             Gotham Globe offices  Los Angeles     USA   
14                  Knebworth House    Knebworth      UK   
15         Acton Lane Power Station        Acton      UK   

             coordinates  travel_time  
0     (55.8642, -4.2518)         8.60  
1     (53.4084, -2.9916)         8.81  
2     (53.4084, -2.9916)         8.81  
3    (41.8781, -87.6298)         2.68  
4      (52.1325, 0.1325)         9.16  
5      (51.5206, -0.134)         9.17  
6   (34.0689, -118.3551)         6.79  
7    (41.8843, -87.6258)         2.68  
8   (34.0689, -118.3551)         6.79  
9   (34.0689, -118.3551)         6.79  
10  (34.0689, -118.3551)         6.79  
11  (34.0689, -118.3551)         6.79  
12  (34.0689, -118.3551)         6.79  
13  (34.0689, -118.3551)         6.79  
14    (51.8833, -0.1333)         9.15  
15    (51.5034, -0.2222)         9.16  

Out - Final answer:                                name         city country  \
0               Necropolis Cemetery      Glasgow      UK   
1                 St. George's Hall    Liverpool      UK   
2   Royal Liver Building, Pier Head    Liverpool      UK   
3                Chicago (exterior)      Chicago     USA   
4                Cardington Studios   Cardington      UK   
5             Central Saint Martins       London      UK   
6                     Bronson Caves  Los Angeles     USA   
7                   Thompson Center      Chicago     USA   
8            Wayne Manor (exterior)  Los Angeles     USA   
9              Cliffs of Marineland  Los Angeles     USA   
10                   Kirkeby Center  Los Angeles     USA   
11            Gateway East Building  Los Angeles     USA   
12              Axis Chemical Works  Los Angeles     USA   
13             Gotham Globe offices  Los Angeles     USA   
14                  Knebworth House    Knebworth      UK   
15         Acton Lane Power Station        Acton      UK   

             coordinates  travel_time  
0     (55.8642, -4.2518)         8.60  
1     (53.4084, -2.9916)         8.81  
2     (53.4084, -2.9916)         8.81  
3    (41.8781, -87.6298)         2.68  
4      (52.1325, 0.1325)         9.16  
5      (51.5206, -0.134)         9.17  
6   (34.0689, -118.3551)         6.79  
7    (41.8843, -87.6258)         2.68  
8   (34.0689, -118.3551)         6.79  
9   (34.0689, -118.3551)         6.79  
10  (34.0689, -118.3551)         6.79  
11  (34.0689, -118.3551)         6.79  
12  (34.0689, -118.3551)         6.79  
13  (34.0689, -118.3551)         6.79  
14    (51.8833, -0.1333)         9.15  
15    (51.5034, -0.2222)         9.16  

[Step 9: Duration 27.16 seconds| Input tokens: 131,299 | Output tokens: 14,742]

                               name         city country  \
0               Necropolis Cemetery      Glasgow      UK   
1                 St. George's Hall    Liverpool      UK   
2   Royal Liver Building, Pier Head    Liverpool      UK   
3                Chicago (exterior)      Chicago     USA   
4                Cardington Studios   Cardington      UK   
5             Central Saint Martins       London      UK   
6                     Bronson Caves  Los Angeles     USA   
7                   Thompson Center      Chicago     USA   
8            Wayne Manor (exterior)  Los Angeles     USA   
9              Cliffs of Marineland  Los Angeles     USA   
10                   Kirkeby Center  Los Angeles     USA   
11            Gateway East Building  Los Angeles     USA   
12              Axis Chemical Works  Los Angeles     USA   
13             Gotham Globe offices  Los Angeles     USA   
14                  Knebworth House    Knebworth      UK   
15         Acton Lane Power Station     

In [24]:
detailed_report

name         city country  \
0               Necropolis Cemetery      Glasgow      UK   
1                 St. George's Hall    Liverpool      UK   
2   Royal Liver Building, Pier Head    Liverpool      UK   
3                Chicago (exterior)      Chicago     USA   
4                Cardington Studios   Cardington      UK   
5             Central Saint Martins       London      UK   
6                     Bronson Caves  Los Angeles     USA   
7                   Thompson Center      Chicago     USA   
8            Wayne Manor (exterior)  Los Angeles     USA   
9              Cliffs of Marineland  Los Angeles     USA   
10                   Kirkeby Center  Los Angeles     USA   
11            Gateway East Building  Los Angeles     USA   
12              Axis Chemical Works  Los Angeles     USA   
13             Gotham Globe offices  Los Angeles     USA   
14                  Knebworth House    Knebworth      UK   
15         Acton Lane Power Station        Acton      UK   

             coordinates  travel_time  
0     (55.8642, -4.2518)         8.60  
1     (53.4084, -2.9916)         8.81  
2     (53.4084, -2.9916)         8.81  
3    (41.8781, -87.6298)         2.68  
4      (52.1325, 0.1325)         9.16  
5      (51.5206, -0.134)         9.17  
6   (34.0689, -118.3551)         6.79  
7    (41.8843, -87.6258)         2.68  
8   (34.0689, -118.3551)         6.79  
9   (34.0689, -118.3551)         6.79  
10  (34.0689, -118.3551)         6.79  
11  (34.0689, -118.3551)         6.79  
12  (34.0689, -118.3551)         6.79  
13  (34.0689, -118.3551)         6.79  
14    (51.8833, -0.1333)         9.15  
15    (51.5034, -0.2222)         9.16

Thanks to these quick changes, we obtained a much more concise report by simply providing our agent a detailed prompt, and giving it planning capabilities!

💸 But as you can see, the context window is quickly filling up. So **if we ask our agent to combine the results of detailed search with another, it will be slower and quickly ramp up tokens and costs**.

➡️ We need to improve the structure of our system.

## ✌️ Splitting the task between two agents

Multi-agent structures allow to separate memories between different sub-tasks, with two great benefits:
- Each agent is more focused on its core task, thus more performant
- Separating memories reduces the count of input tokens at each step, thus reducing latency and cost.

Let's create a team with a dedicated web search agent, managed by another agent.

The manager agent should have plotting capabilities to redact its final report: so let us give it access to additional imports, including `plotly`, and `geopandas` + `shapely` for spatial plotting.

In [29]:
model = InferenceClientModel(
    "Qwen/Qwen2.5-Coder-32B-Instruct", provider="together", max_tokens=8096
)

web_agent = CodeAgent(
    model=model,
    tools=[
        GoogleSearchTool(provider="serpapi"),
        VisitWebpageTool(),
        calculate_cargo_travel_time,
    ],
    name="web_agent",
    description="Browses the web to find information",
    verbosity_level=0,
    max_steps=10,
)

The manager agent will need to do some mental heavy lifting.

So we give it the stronger model [DeepSeek-R1](https://huggingface.co/deepseek-ai/DeepSeek-R1), and add a `planning_interval` to the mix.

In [30]:
import os
OPENAI_API_KEY = os.getenv('OPENAI_API_KEY')

In [31]:
from smolagents.utils import encode_image_base64, make_image_url
from smolagents import OpenAIServerModel


def check_reasoning_and_plot(final_answer, agent_memory):
    multimodal_model = OpenAIServerModel("gpt-4o", max_tokens=8096)
    filepath = "saved_map.png"
    assert os.path.exists(filepath), "Make sure to save the plot under saved_map.png!"
    image = Image.open(filepath)
    prompt = (
        f"Here is a user-given task and the agent steps: {agent_memory.get_succinct_steps()}. Now here is the plot that was made."
        "Please check that the reasoning process and plot are correct: do they correctly answer the given task?"
        "First list reasons why yes/no, then write your final decision: PASS in caps lock if it is satisfactory, FAIL if it is not."
        "Don't be harsh: if the plot mostly solves the task, it should pass."
        "To pass, a plot should be made using px.scatter_map and not any other method (scatter_map looks nicer)."
    )
    messages = [
        {
            "role": "user",
            "content": [
                {
                    "type": "text",
                    "text": prompt,
                },
                {
                    "type": "image_url",
                    "image_url": {"url": make_image_url(encode_image_base64(image))},
                },
            ],
        }
    ]
    output = multimodal_model(messages).content
    print("Feedback: ", output)
    if "FAIL" in output:
        raise Exception(output)
    return True


manager_agent = CodeAgent(
    model=InferenceClientModel("deepseek-ai/DeepSeek-R1", provider="together", max_tokens=8096),
    tools=[calculate_cargo_travel_time],
    managed_agents=[web_agent],
    additional_authorized_imports=[
        "geopandas",
        "plotly",
        "shapely",
        "json",
        "pandas",
        "numpy",
    ],
    planning_interval=5,
    verbosity_level=2,
    final_answer_checks=[check_reasoning_and_plot],
    max_steps=15,
)

Let us inspect what this team looks like:

In [32]:
manager_agent.visualize()

CodeAgent | deepseek-ai/DeepSeek-R1
├── ✅ Authorized imports: ['geopandas', 'plotly', 'shapely', 'json', 'pandas', 'numpy']
├── 🛠️ Tools:
│   ┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
│   ┃ Name                        ┃ Description                           ┃ Arguments                             ┃
│   ┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│   │ calculate_cargo_travel_time │ Calculate the travel time for a cargo │ origin_coords (`array`): Tuple of     │
│   │                             │ plane between two points on Earth     │ (latitude, longitude) for the         │
│   │                             │ using great-circle distance.          │ starting point                        │
│   │                             │                                       │ destination_coords (`array`): Tuple   │
│   │                             │                                       │ of (latitude, longitude) for the      │
│   │                             │                                       │ destination                           │
│   │                             │                                       │ cruising_speed_kmh (`number`):        │
│   │                             │                                       │ Optional cruising speed in km/h       │
│   │                             │                                       │ (defaults to 750 km/h for typical     │
│   │                             │                                       │ cargo planes)                         │
│   │ final_answer                │ Provides a final answer to the given  │ answer (`any`): The final answer to   │
│   │                             │ problem.                              │ the problem                           │
│   └─────────────────────────────┴───────────────────────────────────────┴───────────────────────────────────────┘
└── 🤖 Managed agents:
    └── web_agent | CodeAgent | Qwen/Qwen2.5-Coder-32B-Instruct
        ├── ✅ Authorized imports: []
        ├── 📝 Description: Browses the web to find information
        └── 🛠️ Tools:
            ┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
            ┃ Name                        ┃ Description                       ┃ Arguments                         ┃
            ┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
            │ web_search                  │ Performs a google web search for  │ query (`string`): The search      │
            │                             │ your query then returns a string  │ query to perform.                 │
            │                             │ of the top search results.        │ filter_year (`integer`):          │
            │                             │                                   │ Optionally restrict results to a  │
            │                             │                                   │ certain year                      │
            │ visit_webpage               │ Visits a webpage at the given url │ url (`string`): The url of the    │
            │                             │ and reads its content as a        │ webpage to visit.                 │
            │                             │ markdown string. Use this to      │                                   │
            │                             │ browse webpages.                  │                                   │
            │ calculate_cargo_travel_time │ Calculate the travel time for a   │ origin_coords (`array`): Tuple of │
            │                             │ cargo plane between two points on │ (latitude, longitude) for the     │
            │                             │ Earth using great-circle          │ starting point                    │
            │                             │ distance.     

In [34]:
manager_agent.run("""
Find all Batman filming locations in the world, calculate the time to transfer via cargo plane to here (we're in Gotham, 40.7128° N, 74.0060° W).
Also give me some supercar factories with the same cargo plane transfer time. You need at least 6 points in total.
Represent this as spatial map of the world, with the locations represented as scatter points with a color that depends on the travel time, and save it to saved_map.png!

Here's an example of how to plot and return a map:
import plotly.express as px
df = px.data.carshare()
fig = px.scatter_map(df, lat="centroid_lat", lon="centroid_lon", text="name", color="peak_hour", size=100,
     color_continuous_scale=px.colors.sequential.Magma, size_max=15, zoom=1)
fig.show()
fig.write_image("saved_image.png")
final_answer(fig)

Never try to process strings using code: when you have a string to read, just print it and you'll see it.
""")

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ Find all Batman filming locations in the world, calculate the time to transfer via cargo plane to here (we're   │
│ in Gotham, 40.7128° N, 74.0060° W).                                                                             │
│ Also give me some supercar factories with the same cargo plane transfer time. You need at least 6 points in     │
│ total.                                                                                                          │
│ Represent this as spatial map of the world, with the locations represented as scatter points with a color that  │
│ depends on the travel time, and save it to saved_map.png!                                                       │
│                                                                                                                 │
│ Here's an example of how to plot and return a map:                                                              │
│ import plotly.express as px                                                                                     │
│ df = px.data.carshare()                                                                                         │
│ fig = px.scatter_map(df, lat="centroid_lat", lon="centroid_lon", text="name", color="peak_hour", size=100,      │
│      color_continuous_scale=px.colors.sequential.Magma, size_max=15, zoom=1)                                    │
│ fig.show()                                                                                                      │
│ fig.write_image("saved_image.png")                                                                              │
│ final_answer(fig)                                                                                               │
│                                                                                                                 │
│ Never try to process strings using code: when you have a string to read, just print it and you'll see it.       │
│                                                                                                                 │
╰─ InferenceClientModel - deepseek-ai/DeepSeek-R1 ────────────────────────────────────────────────────────────────╯

────────────────────────────────────────────────── Initial plan ───────────────────────────────────────────────────
Here are the facts I know and the plan of action that I will follow to solve the task:
```
<think>
We are given a task that involves several parts:
1. Find all Batman filming locations in the world.
2. Calculate the time to transfer via cargo plane from Gotham (40.7128° N, 74.0060° W) to each of these locations.
3. Also find some supercar factories that have the same cargo plane transfer time (i.e., the same travel time as 
one of the Batman filming locations? or perhaps we need to find supercar factories that are at locations with 
travel times that match the travel times we have for the Batman locations? The task says "with the same cargo plane
transfer time", meaning we need to find supercar factories that have a travel time from Gotham that matches one of 
the travel times we have for the Batman locations? But note: we need at least 6 points in total. So we might have 
to combine Batman locations and supercar factories to get at least 6 points. However, the task says "also give me 
some supercar factories with the same cargo plane transfer time", meaning we are to find supercar factories that 
have a travel time that is the same as one of the Batman locations? But note: we are to have at least 6 points in 
total. So if we have, say, 4 Batman locations, we might need 2 supercar factories that have travel times matching 
two of those Batman locations? But the task doesn't specify that the travel time must be the same as one of the 
Batman locations. It says "the same cargo plane transfer time", which is ambiguous. However, note that the task 
says "calculate the time to transfer via cargo plane to here (we're in Gotham)" for the Batman locations, and then 
for the supercar factories we are to give them with the same cargo plane transfer time. This likely means that we 
are to find supercar factories that have the same travel time as the Batman locations? But which one? The task 
doesn't specify. Alternatively, it might mean that we are to find supercar factories and calculate their travel 
time from Gotham, and then we are to present at least 6 points (which are a combination of Batman locations and 
supercar factories) and we will color them by travel time. Then the "same" might be a bit misleading. Let me 
re-read: "Also give me some supercar factories with the same cargo plane transfer time." It might be that we are to
find supercar factories that have a travel time that is the same as the travel time we have for the Batman 
locations? But note: we are to have at least 6 points in total. So if we have 3 Batman locations, we might need 3 
supercar factories that have the same travel time as each of the Batman locations? That would be 6 points. But that
seems very restrictive. Alternatively, the task might mean: we are to find Batman locations and then for each 
travel time we have (from the Batman locations) we find a supercar factory that has that same travel time? But 
note: we need at least 6 points. So we might have to find multiple supercar factories per Batman location? The task
is ambiguous. However, note the example output: we are to create a spatial map with scatter points colored by 
travel time. So we can have multiple points with the same travel time. Therefore, I think the intended meaning is: 
we are to find Batman filming locations and calculate their travel times from Gotham. Then we are to find supercar 
factories that are located such that their travel time from Gotham is the same as one of the travel times we have 
for the Batman locations. And we need at least 6 points in total. So if we have 4 Batman locations, we might need 2
supercar factories that have travel times that match two of the Batman locations (so that we have 6 points). But 
note: we might have multiple supercar factories for one travel time. Alternatively, we might have to find supercar 
factories that have travel times tha

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

Output message of the LLM: ────────────────────────────────────────────────────────────────────────────────────────
<think>                                                                                                            
We are going to break down the task into multiple steps. We'll use the `web_agent` tool to find the necessary      
information and then process it.                                                                                   
                                                                                                                   
Step 1: Find Batman filming locations (place names)                                                                
Step 2: For each Batman location, get its coordinates (latitude, longitude)                                        
Step 3: Calculate travel time from Gotham (40.7128, -74.0060) to each Batman location                              
Step 4: Find supercar factory locations (place names)                                                              
Step 5: For each supercar factory, get its coordinates                                                             
Step 6: Calculate travel time from Gotham to each supercar factory                                                 
Step 7: Match supercar factories to Batman locations by travel time (with tolerance) until we have at least 6      
points in total and at least one supercar factory                                                                  
Step 8: Create a combined list of points with details                                                              
Step 9: Plot the map and save it                                                                                   
                                                                                                                   
We'll do these steps in code blocks. However, note that we cannot run too many `web_agent` calls in one block      
because of the unpredictability of the output. We'll break the steps into multiple code blocks.                    
                                                                                                                   
Let's start with Step 1: Find Batman filming locations.                                                            
                                                                                                                   
We'll use the `web_agent` to search for [38;2;230;237;243;48;2;13;17;23

─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  batman_locations_str = web_agent("Find a list of filming locations for Batman movies (like The Dark Knight       
  trilogy, Batman v Superman, etc.) around the world. Please provide the list as a comma-separated list of place   
  names.")                                                                                                         
                                                                                                                   
  # Step 1: Get Batman filming locations                                                                           
  batman_locations_str = web_agent("Provide a comma-separated list of filming locations for Batman movies (such    
  as The Dark Knight, Batman Begins, etc.) around the world. Only include the place names, separated by commas.")  
  print(batman_locations_str)                                                                                      
                                                                                                                   
  batman_locations_str = web_agent("Find a list of filming locations for Batman movies. Please list the place      
  names, one per line or comma separated.")                                                                        
  print(batman_locations_str)                                                                                      
                                                                                                                   
  # For a given location name, we ask for the coordinates                                                          
  coord_str = web_agent(f"What are the latitude and longitude coordinates of {location}? Please provide in the     
  format 'latitude, longitude' in decimal degrees.")                                                               
                                                                                                                   
  import re                                                                                                        
                                                                                                                   
  def parse_coordinates(coord_str):                                                                                
      # Try to find two numbers in the string                                                                      
      pattern = r'[-+]?\d*\.\d+|\d+'                                                                               
      numbers = re.findall(pattern, coord_str)                                                                     
      if len(numbers) >= 2:                                                                                        
          lat = float(numbers[0])                                                                                  
          lon = float(numbers[1])                                                                                  
          return (lat, lon)                                                                                        
      else:                                                                                                        
          return None                                                                                              
                                                                                                                   
  batman_locations = web_agent("Find a comprehensive list of filming locations for Batman movies (including The    
  Dark Knight trilogy, Batman v Superman, etc.) around the world. Include both city names and specific             
  landmarks.")                                                                                                     
  print(batman_locations)                                

...

Code execution failed at line 'fig = plotly.express.scatter_mapbox(...)' due to: AttributeError: module 'plotly' 
has no attribute 'express'

[Step 15: Duration 55.00 seconds| Input tokens: 347,490 | Output tokens: 27,035]

Reached max steps.

[Step 16: Duration 63.86 seconds| Input tokens: 386,848 | Output tokens: 30,465]

'<think>\nWe have encountered multiple issues with the tool calls, primarily due to import restrictions and token limits. \n However, we have collected the necessary data for Batman filming locations and supercar factories. \n We have 4 Batman locations and 5 supercar factories, making a total of 9 points. \n The travel times for Batman locations are: [2.68, 9.17, 1.74, 20.0] hours.\n The supercar factories have travel times: [9.42, 9.35, 9.12, 9.25, 9.05] hours.\n\n Since we cannot use plotly due to import issues, and we are required to save as a PNG, we need an alternative approach.\n\n However, note that the task requires saving to `saved_map.png`. Given the constraints, we might not be able to generate the map via code in this environment.\n\n But note: the example provided uses plotly.express and writes an image. We are allowed to use plotly.express? \n But in previous attempts, we got import errors for plotly.express and plotly.graph_objects.\n\n Given the repeated failures, we w

I don't know how that went in your run, but in mine, the manager agent skilfully divided tasks given to the web agent in `1. Search for Batman filming locations`, then `2. Find supercar factories`, before aggregating the lists and plotting the map.

Let's see what the map looks like by inspecting it directly from the agent state:

In [ ]:
manager_agent.python_executor.state["fig"]

In [35]:
manager_agent.python_executor.state["fig"]

{'data': [{'type': 'scattermapbox',
   'lat': 0    41.8781
   1    51.5074
   2    40.4406
   3    22.3193
   4    44.5955
   5    44.5000
   6    51.3750
   7    51.3397
   8    48.6950
   Name: lat, dtype: float64,
   'lon': 0    -87.6298
   1     -0.1278
   2    -79.9959
   3    114.1694
   4     10.8667
   5     11.6667
   6     -0.5750
   7     12.3731
   8      7.7433
   Name: lon, dtype: float64,
   'mode': 'markers+text',
   'marker': {'size': 15,
    'color': 0     2.68
    1     9.17
    2     1.74
    3    20.00
    4     9.42
    5     9.35
    6     9.12
    7     9.25
    8     9.05
    Name: travel_time, dtype: float64,
    'colorscale': 'Magma',
    'showscale': True,
    'colorbar': {'title': 'Travel Time (hours)'}},
   'text': 0           Chicago, Illinois, USA (Batman) - 2.68 hrs
   1              London, England, UK (Batman) - 9.17 hrs
   2    Pittsburgh, Pennsylvania, USA (Batman) - 1.74 hrs
   3                Hong Kong, China (Batman) - 20.00 hrs
   4    Ferrari 

![output map](https://huggingface.co/datasets/agents-course/course-images/resolve/main/en/unit2/smolagents/output_map.png)